In [1]:
! uv pip install nbdistributed

Using Python 3.11.13 environment at: /usr
Resolved 122 packages in 817ms                                       
⠙ Preparing packages... (0/8)                                                   
⠙ Preparing packages... (0/8)----     0 B/11.56 KiB                     
ipython-pygments-lexers ------------------------------     0 B/7.88 KiB
⠙ Preparing packages... (0/8)----     0 B/11.56 KiB                     
ipython-pygments-lexers ------------------------------     0 B/7.88 KiB
⠙ Preparing packages... (0/8) 11.56 KiB/11.56 KiB                   
ipython-pygments-lexers ------------------------------ 7.88 KiB/7.88 KiB
⠙ Preparing packages... (0/8) 11.56 KiB/11.56 KiB                   
ipython-pygments-lexers ------------------------------ 7.88 KiB/7.88 KiB
pure-eval  ------------------------------ 11.56 KiB/11.56 KiB
⠙ Preparing packages... (0/8)----     0 B/83.36 KiB                     
ipython-pygments-lexers ------------------------------ 7.88 KiB/7.88 KiB
pure-eval  --------------

Load the `nbdistributed` extension to start working with multiple GPUs.

In [2]:
%load_ext nbdistributed

In [3]:
%dist_init --num-processes=2 --gpu-ids 0,1

Using GPU IDs: [0, 1]
Starting 2 distributed workers...
✓ Successfully started 2 workers
  Rank 0 -> GPU 0
  Rank 1 -> GPU 1
Available commands:
  %%distributed - Execute code on all ranks (explicit)
  %%rank [0,n] - Execute code on specific ranks
  %sync - Synchronize all ranks
  %dist_status - Show worker status
  %dist_mode - Toggle automatic distributed mode
  %dist_shutdown - Shutdown workers

🚀 Distributed mode active: All cells will now execute on workers automatically!
   Magic commands (%, %%) will still execute locally as normal.

🐍 Below are auto-imported and special variables auto-generated into the namespace to use
  `torch`
  `dist`: `torch.distributed` import alias
  `rank` (`int`): The local rank
  `world_size` (`int`): The global world size
  `gpu_id` (`int`): The specific GPU ID assigned to this worker
  `device` (`torch.device`): The current PyTorch device object (e.g. `cuda:1`)


<IPython.core.display.Javascript object>

In [4]:
%dist_status

Distributed cluster status (2 processes):
Rank 0: ✓ PID 123
  ├─ GPU: 0 (Tesla T4)
  └─ Status: Running

Rank 1: ✓ PID 124
  ├─ GPU: 1 (Tesla T4)
  └─ Status: Running



<IPython.core.display.Javascript object>

`dist_status` gives us a peek into the state of GPUs we are currently connected to.

In [5]:
%%rank [0]
t = torch.tensor([1,2,3]).to(device)
t


🔹 Rank 0:
  tensor([1, 2, 3], device='cuda:0')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [6]:
device


🔹 Rank 0:
  0

🔹 Rank 1:
  1


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [7]:
%%rank [1]
t = torch.tensor([1,2,3]).to(device)
t


🔹 Rank 1:
  tensor([1, 2, 3], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

We see that there are two tensors created on the GPUs despite the same variable names. This is strange to follow and could be an anti-pattern.

In [8]:
%%rank [1]
b = torch.tensor([1,3,4]).to(device)
b


🔹 Rank 1:
  tensor([1, 3, 4], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [9]:
t + b


🔹 Rank 1:
  tensor([2, 5, 7], device='cuda:1')

❌ Error on Rank 0: name 'b' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 'b' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

This code is failing because the tensor `b` is unavailable on rank0 which is the default way in which the `nbdistributed` package works from the notebook if we do not specify the GPU.

In [10]:
%%rank [1]
t + b


🔹 Rank 1:
  tensor([2, 5, 7], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

If we specify the GPU, the notebook is able to look up with the specific GPU, identify the tensors and do the math!

In [11]:
%dist_shutdown

Shutting down distributed workers (nuclear option)...
Starting force shutdown...
Force shutdown completed
Distributed workers shutdown
📱 Normal cell execution restored


<IPython.core.display.Javascript object>

In [12]:
t

tensor([0, 0, 0])

<IPython.core.display.Javascript object>

It looks like `t` is available because of rank 0 tensor while `b` is most likely not.

In [13]:
b

NameError: name 'b' is not defined

<IPython.core.display.Javascript object>

In [ ]:
%dist_status

# Eyes-off

In [15]:
%load_ext nbdistributed

The nbdistributed extension is already loaded. To reload it, use:
  %reload_ext nbdistributed


<IPython.core.display.Javascript object>

In [16]:
%dist_init --num-processes 2 --gpu-ids 0,1

Using GPU IDs: [0, 1]
Starting 2 distributed workers...
✓ Successfully started 2 workers
  Rank 0 -> GPU 0
  Rank 1 -> GPU 1
Available commands:
  %%distributed - Execute code on all ranks (explicit)
  %%rank [0,n] - Execute code on specific ranks
  %sync - Synchronize all ranks
  %dist_status - Show worker status
  %dist_mode - Toggle automatic distributed mode
  %dist_shutdown - Shutdown workers

🚀 Distributed mode active: All cells will now execute on workers automatically!
   Magic commands (%, %%) will still execute locally as normal.

🐍 Below are auto-imported and special variables auto-generated into the namespace to use
  `torch`
  `dist`: `torch.distributed` import alias
  `rank` (`int`): The local rank
  `world_size` (`int`): The global world size
  `gpu_id` (`int`): The specific GPU ID assigned to this worker
  `device` (`torch.device`): The current PyTorch device object (e.g. `cuda:1`)


<IPython.core.display.Javascript object>

In [17]:
%dist_status

Distributed cluster status (2 processes):
Rank 0: ✓ PID 149
  ├─ GPU: 0 (Tesla T4)
  └─ Status: Running

Rank 1: ✓ PID 150
  ├─ GPU: 1 (Tesla T4)
  └─ Status: Running



<IPython.core.display.Javascript object>

In [18]:
%%rank [0]
t1 = torch.tensor([1,2,3,4,4,5,5])
t1


🔹 Rank 0:
  tensor([1, 2, 3, 4, 4, 5, 5])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [19]:
%%rank [1]
t2 = torch.tensor([1,2,3,4,4,5,5])
t2


🔹 Rank 1:
  tensor([1, 2, 3, 4, 4, 5, 5])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [20]:
t1 + t2


❌ Error on Rank 0: name 't2' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't2' is not defined


❌ Error on Rank 1: name 't1' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't1' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

This wouldn't work because the tensors are on two different devices

In [21]:
%%rank [1]
t3 = torch.tensor([1,2,3,4,4,5,5])
t3


🔹 Rank 1:
  tensor([1, 2, 3, 4, 4, 5, 5])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [22]:
%%rank [1]
t2 + t3


🔹 Rank 1:
  tensor([ 2,  4,  6,  8,  8, 10, 10])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [23]:
%%rank [0]
t2 + t3


❌ Error on Rank 0: name 't2' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't2' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

This wouldn't work as t2 is unavailable on rank 0 device.

In [24]:
t2 + t3


🔹 Rank 1:
  tensor([ 2,  4,  6,  8,  8, 10, 10])

❌ Error on Rank 0: name 't2' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't2' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

The tensors are being added but gathering the result to print needs to bring the result to come to device 0 which is unspecified.

In [25]:
%dist_mode

Distributed mode is currently enabled
Use %dist_mode --enable or %dist_mode --disable to toggle


<IPython.core.display.Javascript object>

In [26]:
%%dist_shutdown

UsageError: Cell magic `%%dist_shutdown` not found (But line magic `%dist_shutdown` exists, did you mean that instead?).


<IPython.core.display.Javascript object>

In [27]:
t1


🔹 Rank 0:
  tensor([1, 2, 3, 4, 4, 5, 5])

❌ Error on Rank 1: name 't1' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't1' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [28]:
t2


🔹 Rank 1:
  tensor([1, 2, 3, 4, 4, 5, 5])

❌ Error on Rank 0: name 't2' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't2' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [29]:
t3


🔹 Rank 1:
  tensor([1, 2, 3, 4, 4, 5, 5])

❌ Error on Rank 0: name 't3' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't3' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Distributed Operations
1. Broadcast
2. Point -> Point
   - 2.1 Synchronous
   - 2.2 Asynchronous
3. One -> All
4. Reduction
   - 3.1 All -> All
   - 3.2 All -> One
5. Gather

In [30]:
%dist_init --num-processes 2 --gpu-ids 0,1

Distributed workers already running. Use %dist_shutdown to stop them first.


<IPython.core.display.Javascript object>

## 1. Broadcast

In [31]:
%%rank [0]
t1 = torch.tensor([1,2,3,4,5], dtype=torch.float32).to(device)
t1


🔹 Rank 0:
  tensor([1., 2., 3., 4., 5.], device='cuda:0')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [32]:
%%rank [1]
t1 = torch.ones(5, dtype=torch.float32).mul(3).to(device) 

t2 = torch.ones(5, dtype=torch.float32).mul(4).to(device)
t1, t2


🔹 Rank 1:
  (tensor([3., 3., 3., 3., 3.], device='cuda:1'), tensor([4., 4., 4., 4., 4.], device='cuda:1'))


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

The broadcast operation broadcasts the t1 tensor from src device to all other devices. 

This operation also over-writes all the other similarly named tensors on the destination devices.

In [33]:
dist.broadcast(t1, src=0)
t1


🔹 Rank 0:
  tensor([1., 2., 3., 4., 5.], device='cuda:0')

🔹 Rank 1:
  tensor([1., 2., 3., 4., 5.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [34]:
%%rank [1]
t1, t2


🔹 Rank 1:
  (tensor([1., 2., 3., 4., 5.], device='cuda:1'), tensor([4., 4., 4., 4., 4.], device='cuda:1'))


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

We see that the `t1` tensor on the device 1 is replaced by the `t1` tensor from device 0.

In [35]:
%dist_status

Distributed cluster status (2 processes):
Rank 0: ✓ PID 149
  ├─ GPU: 0 (Tesla T4)
  ├─ Memory: 0.0GB / 14.7GB (0.0% used)
  ├─ Reserved: 0.0GB
  └─ Status: Running

Rank 1: ✓ PID 150
  ├─ GPU: 1 (Tesla T4)
  ├─ Memory: 0.0GB / 14.7GB (0.0% used)
  ├─ Reserved: 0.0GB
  └─ Status: Running



<IPython.core.display.Javascript object>

In [36]:
def tinfo(t, before=True):
    word = "before" if before else "after"
    print(f"""Rank: {rank} tensor {word} op:
    - Shape: {t.shape}
    - Device: {t.device}
    - Dtype: {t.dtype}
    - Value: {t}
""")

tinfo(t1)


🔹 Rank 0:
  Rank: 0 tensor before op:
    - Shape: torch.Size([5])
    - Device: cuda:0
    - Dtype: torch.float32
    - Value: tensor([1., 2., 3., 4., 5.], device='cuda:0')

🔹 Rank 1:
  Rank: 1 tensor before op:
    - Shape: torch.Size([5])
    - Device: cuda:1
    - Dtype: torch.float32
    - Value: tensor([1., 2., 3., 4., 5.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [37]:
tinfo(t2)


🔹 Rank 1:
  Rank: 1 tensor before op:
    - Shape: torch.Size([5])
    - Device: cuda:1
    - Dtype: torch.float32
    - Value: tensor([4., 4., 4., 4., 4.], device='cuda:1')

❌ Error on Rank 0: name 't2' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't2' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [38]:
tinfo(t3)


🔹 Rank 1:
  Rank: 1 tensor before op:
    - Shape: torch.Size([7])
    - Device: cpu
    - Dtype: torch.int64
    - Value: tensor([1, 2, 3, 4, 4, 5, 5])

❌ Error on Rank 0: name 't3' is not defined
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 284, in _execute_code_streaming
    result = eval(compile(tree, '<string>', 'eval'), self.namespace)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<string>", line 1, in <module>
NameError: name 't3' is not defined



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## 2. Point -> Point 

### 2.1 Synchronous

There are times when data is sent from device A to device B and not others.

In [39]:
%dist_shutdown

Shutting down distributed workers (nuclear option)...
Starting force shutdown...
Force shutdown completed
Distributed workers shutdown
📱 Normal cell execution restored


<IPython.core.display.Javascript object>

In [40]:
%dist_init --num-processes 2 --gpu-ids 0,1

Using GPU IDs: [0, 1]
Starting 2 distributed workers...
✓ Successfully started 2 workers
  Rank 0 -> GPU 0
  Rank 1 -> GPU 1
Available commands:
  %%distributed - Execute code on all ranks (explicit)
  %%rank [0,n] - Execute code on specific ranks
  %sync - Synchronize all ranks
  %dist_status - Show worker status
  %dist_mode - Toggle automatic distributed mode
  %dist_shutdown - Shutdown workers

🚀 Distributed mode active: All cells will now execute on workers automatically!
   Magic commands (%, %%) will still execute locally as normal.

🐍 Below are auto-imported and special variables auto-generated into the namespace to use
  `torch`
  `dist`: `torch.distributed` import alias
  `rank` (`int`): The local rank
  `world_size` (`int`): The global world size
  `gpu_id` (`int`): The specific GPU ID assigned to this worker
  `device` (`torch.device`): The current PyTorch device object (e.g. `cuda:1`)


<IPython.core.display.Javascript object>

In [41]:
def tinfo(t, before=True):
    word = "before" if before else "after"
    print(f"""Rank: {rank} tensor {word} op:
    - Shape: {t.shape}
    - Device: {t.device}
    - Dtype: {t.dtype}
    - Value: {t}
""")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [42]:
if rank == 0:
    t1 = torch.tensor([1,2,3,4,5], dtype=torch.float32).to(device)
    tinfo(t1)
    dist.send(t1, dst=1)
else:
    t1 = torch.ones(5, dtype=torch.float32).mul(3).to(device)
    tinfo(t1)
    dist.recv(t1, src=0)
    tinfo(t1, False)


🔹 Rank 1:
  Rank: 1 tensor before op:
    - Shape: torch.Size([5])
    - Device: cuda:1
    - Dtype: torch.float32
    - Value: tensor([3., 3., 3., 3., 3.], device='cuda:1')

🔹 Rank 0:
  Rank: 0 tensor before op:
    - Shape: torch.Size([5])
    - Device: cuda:0
    - Dtype: torch.float32
    - Value: tensor([1., 2., 3., 4., 5.], device='cuda:0')
  Rank: 1 tensor after op:
    - Shape: torch.Size([5])
    - Device: cuda:1
    - Dtype: torch.float32
    - Value: tensor([1., 2., 3., 4., 5.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### 2.2 Asynchronous

In [43]:
device


🔹 Rank 0:
  0

🔹 Rank 1:
  1


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [44]:
%%rank [0]
a = torch.tensor([1,2,3,4,6], dtype=torch.float32).to(device)
request = dist.isend(a, dst=1)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [45]:
%%rank [1]
a = torch.zeros(5, dtype=torch.float32).to(device)
print(f"a before: {a}")
request = dist.irecv(a, src=0)
print(f"a after: {a}")


🔹 Rank 1:
  a before: tensor([0., 0., 0., 0., 0.], device='cuda:1')
  a after: tensor([1., 2., 3., 4., 6.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [46]:
%%distributed
request.wait()


🔹 Rank 0:
  True

🔹 Rank 1:
  True


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## 3. One -> All

In [47]:
%%rank [0]
a = torch.tensor([1,2,3,4,6], dtype=torch.float32).to(device)
a


🔹 Rank 0:
  tensor([1., 2., 3., 4., 6.], device='cuda:0')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [48]:
%%rank [1]
a = torch.tensor([2,4,5,6,7], dtype=torch.float32).to(device)
a


🔹 Rank 1:
  tensor([2., 4., 5., 6., 7.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [49]:
dist.broadcast(a, src=0)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [50]:
%%rank [1]
a


🔹 Rank 1:
  tensor([1., 2., 3., 4., 6.], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Scatter

In [51]:
%%rank [0]
scatter_list = [torch.tensor([i, i+1]).to(device) for i in range(0, 4, 2)]
scatter_list


🔹 Rank 0:
  [tensor([0, 1], device='cuda:0'), tensor([2, 3], device='cuda:0')]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [52]:
%%rank [1]
scatter_list = None

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [53]:
%%distributed
output = torch.empty(2, dtype=torch.int64).to(device)
dist.scatter(output, scatter_list, src=0)
print(f"rank {rank} received {output}")


🔹 Rank 0:
  rank 0 received tensor([0, 1], device='cuda:0')

🔹 Rank 1:
  rank 1 received tensor([2, 3], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

`output` variable is available on all devices. We will collect the data from `scatter_list` and store it in `output` variable.


`scatter` operation scattered each list element to each device.

In [54]:
%%distributed
output = torch.empty(2, dtype=torch.int64).to(device)
dist.scatter(output, scatter_list, src=0)
print(f"rank {rank} received {output}")


🔹 Rank 0:
  rank 0 received tensor([0, 1], device='cuda:0')

🔹 Rank 1:
  rank 1 received tensor([2, 3], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

`%%distributed` command runs the cell commands on all devices.

## 5. Reduction
### All -> All

In [55]:
# create tensors on each device
# print them
# sum them up using dist.ReduceOp.SUM
# print them

<IPython.core.display.Javascript object>

In [56]:
%dist_shutdown

Shutting down distributed workers (nuclear option)...
Starting force shutdown...
Force shutdown completed
Distributed workers shutdown
📱 Normal cell execution restored


<IPython.core.display.Javascript object>

In [57]:
%dist_init --num-processes 2 --gpu-ids 0,1

Using GPU IDs: [0, 1]
Starting 2 distributed workers...
✓ Successfully started 2 workers
  Rank 0 -> GPU 0
  Rank 1 -> GPU 1
Available commands:
  %%distributed - Execute code on all ranks (explicit)
  %%rank [0,n] - Execute code on specific ranks
  %sync - Synchronize all ranks
  %dist_status - Show worker status
  %dist_mode - Toggle automatic distributed mode
  %dist_shutdown - Shutdown workers

🚀 Distributed mode active: All cells will now execute on workers automatically!
   Magic commands (%, %%) will still execute locally as normal.

🐍 Below are auto-imported and special variables auto-generated into the namespace to use
  `torch`
  `dist`: `torch.distributed` import alias
  `rank` (`int`): The local rank
  `world_size` (`int`): The global world size
  `gpu_id` (`int`): The specific GPU ID assigned to this worker
  `device` (`torch.device`): The current PyTorch device object (e.g. `cuda:1`)


<IPython.core.display.Javascript object>

In [61]:
%%distributed

t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"t before op: {t}")
dist.all_reduce(t, dist.ReduceOp.SUM)
print(f"t after op: {t}")


🔹 Rank 0:
  t before op: tensor([1, 2, 3], device='cuda:0')
  t after op: tensor([3, 5, 7], device='cuda:0')

🔹 Rank 1:
  t before op: tensor([2, 3, 4], device='cuda:1')
  t after op: tensor([3, 5, 7], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [62]:
rank


🔹 Rank 0:
  0

🔹 Rank 1:
  1


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [63]:
gpu_id


🔹 Rank 0:
  0

🔹 Rank 1:
  1


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

All the `t` tensors are getting added (reduce operation) and the result is stored in across all the GPUs.

In [65]:
%%distributed

t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"t before op: {t}")
dist.all_reduce(t, dist.ReduceOp.MAX)
print(f"t after op: {t}")


🔹 Rank 0:
  t before op: tensor([1, 2, 3], device='cuda:0')
  t after op: tensor([2, 3, 4], device='cuda:0')

🔹 Rank 1:
  t before op: tensor([2, 3, 4], device='cuda:1')
  t after op: tensor([2, 3, 4], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [66]:
%%distributed

t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"t before op: {t}")
dist.all_reduce(t, dist.ReduceOp.MIN)
print(f"t after op: {t}")


🔹 Rank 0:
  t before op: tensor([1, 2, 3], device='cuda:0')
  t after op: tensor([1, 2, 3], device='cuda:0')

🔹 Rank 1:
  t before op: tensor([2, 3, 4], device='cuda:1')
  t after op: tensor([1, 2, 3], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## 6. Reduction
### All -> One

In [67]:
# create tensors on all devices
# print them before op
# reduce on one device
# print them after op

<IPython.core.display.Javascript object>

In [68]:
%%distributed

t = torch.tensor([1+rank, 2+rank, 5+rank]).to(device)
print(f"t before op: {t}")
dist.reduce(t, dst=1, op=dist.ReduceOp.SUM)
print(f"t after op: {t}")


🔹 Rank 0:
  t before op: tensor([1, 2, 5], device='cuda:0')
  t after op: tensor([1, 2, 5], device='cuda:0')

🔹 Rank 1:
  t before op: tensor([2, 3, 6], device='cuda:1')
  t after op: tensor([ 3,  5, 11], device='cuda:1')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

We see that the sum of `t` tensors on both the devices is stored only on the destination device but not all devices.

## 7. Gather

`Gather` operation pulls together all the `t` tensors on each device and stores them in one variable. On all devices!

In [69]:
# create a tensor placeholder
# create tensors on all devices
# print them before gather op
# all_gather the tensors to all devices and put it in placeholder tensor
# print them after gather op

<IPython.core.display.Javascript object>

In [73]:
%%distributed

tensor_list = [torch.zeros(3, dtype=torch.int64).to(device) for _ in range(0, 2)]
t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"tensor_list before op: {tensor_list}")
dist.all_gather(tensor_list, t)
print(f"tensor_list after op: {tensor_list}")

torch.cuda.synchronize() # why is this needed?


🔹 Rank 0:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:0'), tensor([0, 0, 0], device='cuda:0')]
  tensor_list after op: [tensor([1, 2, 3], device='cuda:0'), tensor([2, 3, 4], device='cuda:0')]

🔹 Rank 1:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:1'), tensor([0, 0, 0], device='cuda:1')]
  tensor_list after op: [tensor([1, 2, 3], device='cuda:1'), tensor([2, 3, 4], device='cuda:1')]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [74]:
%%distributed

tensor_list = [torch.zeros(3, dtype=torch.int64).to(device) for _ in range(0, 2)]
t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"tensor_list before op: {tensor_list}")
dist.all_gather(tensor_list, t)
print(f"tensor_list after op: {tensor_list}")

torch.cuda.synchronize() # why is this needed?


🔹 Rank 0:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:0'), tensor([0, 0, 0], device='cuda:0')]
  tensor_list after op: [tensor([1, 2, 3], device='cuda:0'), tensor([2, 3, 4], device='cuda:0')]

🔹 Rank 1:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:1'), tensor([0, 0, 0], device='cuda:1')]
  tensor_list after op: [tensor([1, 2, 3], device='cuda:1'), tensor([2, 3, 4], device='cuda:1')]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [104]:
%%distributed

tensor_list = torch.zeros(2, 3, dtype=torch.int64).to(device)
t = torch.tensor([1+rank,4+rank,6+rank], dtype=torch.int64).to(device)
print(f"tensor_list before op: {tensor_list}, rank {rank}")
dist.all_gather_into_tensor(tensor_list, t)
print(f"tensor_list after op: {tensor_list}, rank {rank}")
torch.cuda.synchronize() 


🔹 Rank 0:
  tensor_list before op: tensor([[0, 0, 0],
        [0, 0, 0]], device='cuda:0'), rank 0
  tensor_list after op: tensor([[1, 4, 6],
        [2, 5, 7]], device='cuda:0'), rank 0

🔹 Rank 1:
  tensor_list before op: tensor([[0, 0, 0],
        [0, 0, 0]], device='cuda:1'), rank 1
  tensor_list after op: tensor([[1, 4, 6],
        [2, 5, 7]], device='cuda:1'), rank 1


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
%dist_shutdown

In [109]:
%dist_init --num-processes 2 --gpu-ids 0,1

Using GPU IDs: [0, 1]
Starting 2 distributed workers...
✓ Successfully started 2 workers
  Rank 0 -> GPU 0
  Rank 1 -> GPU 1
Available commands:
  %%distributed - Execute code on all ranks (explicit)
  %%rank [0,n] - Execute code on specific ranks
  %sync - Synchronize all ranks
  %dist_status - Show worker status
  %dist_mode - Toggle automatic distributed mode
  %dist_shutdown - Shutdown workers

🚀 Distributed mode active: All cells will now execute on workers automatically!
   Magic commands (%, %%) will still execute locally as normal.

🐍 Below are auto-imported and special variables auto-generated into the namespace to use
  `torch`
  `dist`: `torch.distributed` import alias
  `rank` (`int`): The local rank
  `world_size` (`int`): The global world size
  `gpu_id` (`int`): The specific GPU ID assigned to this worker
  `device` (`torch.device`): The current PyTorch device object (e.g. `cuda:1`)


<IPython.core.display.Javascript object>

In [110]:
%%distributed

tensor_list = [torch.zeros(3, dtype=torch.int64).to(device) for _ in range(0, 2)]
t = torch.tensor([1+rank, 2+rank, 3+rank]).to(device)
print(f"tensor_list before op: {tensor_list}")
dist.all_gather_into_one(tensor_list, t, dst=1)
print(f"tensor_list after op: {tensor_list}")

torch.cuda.synchronize() # why is this needed?


🔹 Rank 0:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:0'), tensor([0, 0, 0], device='cuda:0')]

🔹 Rank 1:
  tensor_list before op: [tensor([0, 0, 0], device='cuda:1'), tensor([0, 0, 0], device='cuda:1')]

❌ Error on Rank 1: module 'torch.distributed' has no attribute 'all_gather_into_one'
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/nbdistributed/worker.py", line 282, in _execute_code_streaming
    tree = ast.parse(code.strip(), mode='eval')
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/ast.py", line 50, in parse
    return compile(source, filename, mode, flags,
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "<unknown>", line 1
    tensor_list = [torch.zeros(3, dtype=torch.int64).to(device) for _ in range(0, 2)]
                ^
SyntaxError: invalid syntax

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.11/d

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [106]:
# for debugging
# %dist_mode --enable
# %dist_mode --disable

<IPython.core.display.Javascript object>

In [107]:
%dist_shutdown

Shutting down distributed workers (nuclear option)...
Starting force shutdown...
Force shutdown completed
Distributed workers shutdown
📱 Normal cell execution restored


<IPython.core.display.Javascript object>